# Unsupervised Learning - Clustering
## The Objectives
The objective of this unsupervised learning analysis is, through clustering, to try to identify groups of Township-Ranges and their characteristics. Ideally this analysis would help reveal the characteristics of the Township-Ranges with sustainable water situation and those with systemic water problems.

We will try different clustering algorithms:
* K-means
* DBSCAN
* Hierarchical clustering
* UMAP

In [1]:
import sys
sys.path.append('..')

In [2]:
import pandas as pd
import functools
import operator
import altair as alt

from sklearn.preprocessing import MinMaxScaler

from lib.township_range import TownshipRanges
from lib.transform_impute import convert_back_df
from lib.read_data import read_and_join_output_file
from lib.create_pipeline import create_transformation_pipeline
from lib.viz import draw_faceted_lines, view_trs_side_by_side, draw_small_multiples_bar_charts, display_data_on_map, draw_hierarchical_parameters_results
from lib.unsupervised import kmeans_parameters_search, compute_kmeans_clusters_and_features, dbscan_parameters_search, hierarchical_parameters_search, get_most_frequent_cluster, get_most_frequent_cluster_for_all_parameters

In [3]:
alt.data_transformers.disable_max_rows()

DataTransformerRegistry.enable('default')

## Preparing the Dataset for Clustering
We read the data from the resulting from the imputation and scaling pipeline and stored in the pickle file.

The objective of this analysis is to try to cluster the Township-Ranges together in a meaningful way based on their characteristics. Our dataset  is made of one data point per year for each Township-Range. We will try to apply clustering on the dataset as is, essentially clustering all the years of all the Township-Ranges individually (e.g. the Township-Range `T01N R02E` in 2014 might be in one cluster and the same Township-Range in 2015 might be in a different cluster).

Unlike for supervised learning where the `GSE_GWE` feature (the depth to groundwater elevation in feet below ground surface) is the value we are trying to predict, for clustering it could be an important feature to help differentiate Township-Ranges. For this analysis we thus merge it back in the dataset.

Also we use a min-max scaler here not to have mean negative values which might be difficult to interpret.

In [4]:
RANDOM_SEED = 42
township_range = TownshipRanges()
df = read_and_join_output_file()
impute_pipe = create_transformation_pipeline(df, scaler = MinMaxScaler())
X = impute_pipe.fit_transform(df)
X = convert_back_df(
    X,
    impute_pipe,
    df,
)
X.head(16)

TOTALDRILLDEPTH_AVG  WELLYIELD_AVG  STATICWATERLEVEL_AVG  \
TOWNSHIP_RANGE YEAR                                                             
T01N R02E      2014             0.000000       0.000489              0.020868   
               2015             0.000000       0.000000              0.000000   
               2016             0.000000       0.003259              0.036728   
               2017             0.066667       0.006410              0.025876   
               2018             0.053651       0.000652              0.063022   
               2019             0.117460       0.000000              0.029215   
               2020             0.057778       0.006519              0.039399   
               2021             0.000000       0.000000              0.000000   
T01N R03E      2014             0.097778       0.014124              0.037145   
               2015             0.095238       0.016297              0.025042   
               2016             0.114286       0.006128              0.022398   
               2017             0.000000       0.010593              0.030885   
               2018             0.083873       0.001915              0.034558   
               2019             0.078492       0.000000              0.029772   
               2020             0.074325       0.011816              0.030607   
               2021             0.115159       0.054987              0.020987   

                     TOPOFPERFORATEDINTERVAL_AVG  \
TOWNSHIP_RANGE YEAR                                
T01N R02E      2014                     0.052288   
               2015                     0.000000   
               2016                     0.084967   
               2017                     0.082789   
               2018                     0.077124   
               2019                     0.039216   
               2020                     0.072712   
               2021                     0.000000   
T01N R03E      2014                     0.098039   
               2015                     0.117647   
               2016                     0.152614   
               2017                     0.127451   
               2018                     0.148257   
               2019                     0.140359   
               2020                     0.127859   
               2021                     0.148911   

                     BOTTOMOFPERFORATEDINTERVAL_AVG  TOTALCOMPLETEDDEPTH_AVG  \
TOWNSHIP_RANGE YEAR                                                            
T01N R02E      2014                        0.075670                 0.127841   
               2015                        0.000000                 0.000000   
               2016                        0.057471                 0.056818   
               2017                        0.063857                 0.074495   
               2018                        0.052874                 0.064015   
               2019                        0.137931                 0.140152   
               2020                        0.055556                 0.068561   
               2021                        0.000000                 0.000000   
T01N R03E      2014                        0.111111                 0.105455   
               2015                        0.080460                 0.079545   
               2016                        0.103768                 0.104482   
               2017                        0.082375                 0.081439   
               2018                        0.093934                 0.107197   
               2019                        0.094732                 0.093655   
               2020                        0.089320                 0.088684   
               2021                        0.112197                 0.117045   

                     VEGETATION_BLUE_OAK-GRAY_PINE  \
TOWNSHIP_RANGE YEAR                                  
T01N R02E      2014                       0.010798   
               2015   

## Clustering with K-means
### Choosing the Best K-Value
To choose the best `k` value for the K-Means algorithm, we run the K-Means algorithm for different values of `k`between 2 and 10 and evaluate the clustering results based ond the following metrics:
* The Calinski-Harabasz score (the sum of the between-clusters distance to intra-cluster distance, higher values indicate better cluster compactness),
* The Davies-Bouldin score (the average similarity of each cluster, lower values indicate better separation between clusters),
* The Silhouette score (the divergence between clusters considering both intra and inter cluster distances),
* The Sum of Squared Distances of samples to their closest cluster center

In [5]:
X_kmeans = X.copy()
k_estimation_df = kmeans_parameters_search(X_kmeans, max_k=16).rename(
    columns={
        "k": "k",
        "calinski_harabasz_score": "Calinski-Harabasz score (higher is better)",
        "davies_bouldin_score": "Davies-Bouldin score (lower is better)",
        "silhouette_score": "Silhouette score (closer to 1 is better)",
        "sum_squared_distances": "Sum of Squared Distances (lower is better)",
    }
).melt(id_vars=["k"], var_name="metric", value_name="score")
draw_faceted_lines(
    df=k_estimation_df, x="k", y="score", facet="metric",
    title="K-Means Calinski-Harabasz, Davies-Bouldin, Silhouette scores and Sum of Squared Distances for different K values",
    x_title="Number of clusters",
    y_title="score"
)

alt.FacetChart(...)

Based on the above plots of the various clustering metric scores we get
 * the Calinski-Harabasz score (indicating better cluster compactness) is best when __k=2__
 * the Davies-Bouldin score (indicating better separation between clusters) is best when __k=14__ but also very good when __k=2__
 * although the Silhouette scores increases with k, it remains similar (between 0.1 and 0.18), very far from the optimum value of 1
 * the Sum of Squared Distances doesn't show any "elbow" in the plot to help deciding the best value of k

Based on the above clustering metrics, we decided to use __k=2__ as our best value for the K-Means algorithm.

Once we apply K-Means algorithm to generate two clusters using the custom `extract_clusters_features()` function, we can
* see how Township-Ranges are assigned to clusters year by year
* compare the clusters based on their mean on the predominant features (based on their value from the cluster center) of both clusters

### Comparing the Township-Ranges Clustering by Year

In [6]:
kmeans_df, predominant_features = compute_kmeans_clusters_and_features(X_kmeans, k=2, random_state=RANDOM_SEED)
all_predominant_features = dict(sorted(functools.reduce(operator.iconcat, predominant_features , []), key = lambda feature: feature[1]))
sorted_feature_names = list(all_predominant_features.keys())[::-1]
kmeans_df = kmeans_df[sorted_feature_names + ["cluster"]]
#kmeans_df

In [7]:
view_trs_side_by_side(
    pd.merge(township_range.sjv_township_range_df, kmeans_df["cluster"].reset_index(), how="left", on=["TOWNSHIP_RANGE", ]),
    feature="YEAR",
    value="cluster",
    title="Township-Ranges cluster by year",
    color_scheme="sjv")

alt.ConcatChart(...)

### Looking at the Clusters on a Map
If one of the category (represented in blue above) is mainly located on the South-East of the San Joaquin Valley, we want to explore if the two clusters if these Township-Ranges are related to some geographical features by looking at them on a map. As few Township-Ranges change clusters over the year, to display the categories on one single map, we take the most frequent cluster of each Township-Range.

In [8]:
display_data_on_map(get_most_frequent_cluster(kmeans_df, township_range.sjv_township_range_df), feature="cluster", categorical=True, color_scheme="sjv")

### Comparing the Predominant Features of the Two Clusters

In [9]:
feature_comparison_df = kmeans_df.groupby("cluster").mean().reset_index()
feature_comparison_df = feature_comparison_df.melt(id_vars="cluster", value_vars=feature_comparison_df.columns[1:], var_name="feature", value_name="mean")
draw_small_multiples_bar_charts(feature_comparison_df, x="cluster", y="mean",
                                facet="feature", facet_sort=sorted_feature_names,
                                title="Difference in mean values of the most predominant features for each cluster")

alt.FacetChart(...)

### Discussing the K-Means results
The first striking result from clustering the Township-Ranges independently on years is that there are just about 10 Township-Ranges showing some variations in their clustering.
The second one, is that one of the cluster (cluster 0 shown in blue above) is mainly located on the South-East of the San Joaquin Valley, on a axis following the road 99 between the towns of Madera, Fresno, Tulare, Delan and Bakersfield in the Madera, Fresno, Tulare and Kern counties.
Comparing the predominant features in both clusters we see that:
* Township-Ranges in cluster 0 (in blue) have:
  * an average of their land surface covered for more than 65% by *Entisoils* of hydrologic group *B*. According to the [definition *Entisoils*](https://www.nrcs.usda.gov/wps/portal/nrcs/detail/soils/survey/class/maps/?cid=nrcs142p2_053596) are soils with *little, if any horizon development*, *many are sandy and very shallow*. The hydrologic group *B* are soils that have *moderately low runoff potential when thoroughly wet. Water transmission through the soils is unimpended*. In summary sandy and shallow soils letting the water penetrate deeper.
  * higher depth from the ground surface to groundwater (GSE_GWE), meaning that it is required to dig deeper wells to reach groundwater. This is also illustrated by the wells having a deeper top and bottom perforation.
  * have a higher population density, which is normal as  we see that these Township-Ranges are mainly aligned along the road 99, between the towns between Madera and Bakersfield
  * cultivate more of crop *D12* which are almonds and known to be consuming a lot of water
  * have more non-native (i.e. planted) hardwood forest
* Township-Ranges in cluster 1 (in brown) have:
  * in general slightly richer soils with more water runoff potential when wet
    * [*Alfisols*](https://www.nrcs.usda.gov/wps/portal/nrcs/detail/soils/survey/class/maps/?cid=nrcs142p2_053590) of hydrologic group *D*, are *soils that have an argillic, a kandic, or a natric horizon and a base saturation of 35% or greater*. The hydrologic group *D* being soils *with a high runoff potential when thoroughly wet*
    * [*Vertisoils*](https://www.nrcs.usda.gov/wps/portal/nrcs/detail/soils/survey/class/maps/?cid=nrcs142p2_053611) of hydrologic group *D*, are *soils that have a high content of expanding clay*
    * [*Molisoils*]() of hydrologic group *B* are *soils that have a dark colored surface horizon and are base rich*
  * water reservoirs with more capacity
  * higher average yearly precipitation

From the details above it seems that the cluster 0 (in blue) is mainly made of Township-Ranges
* located in the South-East along the road 99, between the towns between Madera and Bakersfield and thus with higher population density,
* have poorer sandy soils
* requires to dig deeper to reach groundwater
* have less precipitation
* have water reservoirs with less capacity

## Clustering with DBSCAN
Like for *K-Means*, to chose the best values for the *eps* and *min_samples* parameters of the *DBSCAN* clustering model, we fit the *DBSCAN* clustering algorithm with a range of values for both parameters and record the following scores and data:
* The Calinski-Harabasz score (the sum of the between-clusters distance to intra-cluster distance, higher values indicate better cluster compactness),
* The Davies-Bouldin score (the average similarity of each cluster, lower values indicate better separation between clusters),
* The Silhouette score (the divergence between clusters considering both intra and inter cluster distances),
* The noise or amount of data points (Township_Range and years) DBSCAN did not assign to any cluster. We obviously do not want that to be too high. By default the custom search filters out results from DBSCAN having a noise value > 100, which is an average of 12.5 Towhnship-Ranges per year which would not belong to any cluster.
* The amount of clusters found. We also do not want this to bee too high as too many clusters will be very difficult to interpret. By default the custom search filters out results with a number of clusters > 5

In [10]:
parameters = {
    "eps": [0.6, 0.7, 0.8, 0.9, 1.0],
    "min_samples": [2, 3, 4, 5, 6, 7, 8, 9]
}
X_dbscan = X.copy()
dbscan_params_estimation_df = dbscan_parameters_search(X_dbscan, eps_list=parameters["eps"], min_samples_list=parameters["min_samples"], max_noise=250)
dbscan_params_estimation_df

eps min_samples  davies_bouldin_score  calinski_harabasz_score  \
0   0.7           9              3.717186                20.922679   
1   0.8           7              2.554410                15.192638   
2   0.8           8              2.491874                15.456429   
3   0.8           9              3.825019                16.368412   
4   0.9           2              1.263106                 9.592943   
5   0.9           3              1.263106                 9.592943   
6   0.9           4              1.270243                 9.834957   
7   0.9           5              2.084858                13.099711   
8   0.9           6              2.210580                13.018431   
9   0.9           7              2.436809                12.794251   
10  0.9           8              2.436809                12.794251   
11  1.0           2              0.748207                11.610496   
12  1.0           3              0.748207                11.610496   
13  1.0           4              0.748207                11.610496   
14  1.0           5              0.748207                11.610496   
15  1.0           6              0.748207                11.610496   
16  1.0           7              0.748207                11.610496   
17  1.0           8              1.393706                12.493338   

    silhouette_score n_clusters  noise  \
0           0.040076          3  193.0   
1           0.061369          5   45.0   
2           0.061498          5   48.0   
3           0.077697          2   74.0   
4           0.094687          5    2.0   
5           0.094687          5    2.0   
6           0.094301          5    3.0   
7           0.161090          3   14.0   
8           0.161823          3   15.0   
9           0.161232          3   17.0   
10          0.161232          3   17.0   
11          0.163036          3    1.0   
12          0.163036          3    1.0   
13          0.163036          3    1.0   
14          0.163036          3    1.0   
15          0.163036          3    1.0   
16          0.163036          3    1.0   
17          0.166663          3    4.0   

                                               labels  
0   [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, ...  
1   [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, ...  
2   [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, ...  
3   [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, ...  
4   [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, ...  
5   [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, ...  
6   [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, ...  
7   [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, ...  
8   [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, ...  
9   [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, ...  
10  [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, ...  
11  [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, ...  
12  [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, ...  
13  [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, ...  
14  [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, ...  
15  [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, ...  
16  [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, ...  
17  [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, ...

Based on the filtering, removing *DBSCAN* parameters creating too much noise or too many clusters, we are left with few combinations of parameters in the table above.
Looking at the table it is hard to find a set of *eps* and *min_samples* values, providing a good compromise between the different scores and amount of *noise*.

For each of the set of parameters, we can compare the resulting clustering by simply taking the most frequent cluster assigned to each Township-Ranges

In [12]:
view_trs_side_by_side(
    get_most_frequent_cluster_for_all_parameters(X_dbscan, dbscan_params_estimation_df, ["eps", "min_samples"], township_range.sjv_township_range_df),
    feature="parameters", value="cluster", title="Comparing the DBSCAN clustering results for each set of paramters", color_scheme="sjv")

alt.ConcatChart(...)

Whatever the set of parameter values, the clustering resulting from *DBSCAN* looks non-informative. All Township-Ranges are clustered into one big clusters (cluster 0 in blue), with very small Township-Ranges clusters of 1~2 Township-Ranges in the North-West or the far South-East.
## Hierarchical Clustering
Here gain, to chose the best values for the *n_clusters*, *affinity* and *linkage* parameters of the hierarcical clustering model, we fit the *AgglomerativeClustering* clustering algorithm with a range of values for both parameters and record the following scores and data:
* The Calinski-Harabasz score (the sum of the between-clusters distance to intra-cluster distance, higher values indicate better cluster compactness),
* The Davies-Bouldin score (the average similarity of each cluster, lower values indicate better separation between clusters),
* The Silhouette score (the divergence between clusters considering both intra and inter cluster distances),

In [20]:
parameters = {
    "affinity": ["euclidean", "l1", "l2", "manhattan", "cosine"],
    "linkage": ["single", "average", "complete", "ward"]
}
X_hierarchical = X.copy()
hierarchical_results_df = hierarchical_parameters_search(X_hierarchical, affinity_list=parameters["affinity"], linkage_list=parameters["linkage"])
hierarchical_scores_df = hierarchical_results_df.copy()
hierarchical_scores_df["x"] = hierarchical_scores_df["affinity"] + "/" + hierarchical_scores_df["linkage"]
hierarchical_scores_df = hierarchical_scores_df[["x", "calinski_harabasz_score", "davies_bouldin_score", "silhouette_score"]].rename(
    columns={
        "calinski_harabasz_score": "Calinski-Harabasz score (higher is better)",
        "davies_bouldin_score": "Davies-Bouldin score (lower is better)",
        "silhouette_score": "Silhouette score (closer to 1 is better)"
    }
).melt(id_vars=["x"], var_name="metric", value_name="score")
draw_hierarchical_parameters_results(df=hierarchical_scores_df,
                                     x="x", y="score", facet="metric", title=["Clustering Scores for the various AgglomerativeClustering parameters", "(sorted by score)"], x_title = "Affinity / Linkage", y_title="score")

alt.FacetChart(...)

As for the *K-Means* clustering method, there is no set of *affinity* and *linkage* parameter values which are optimum for every metric.
* The best (higest) *Calinski-Harabasz* score is obtained for `affinity="euclidean` and `linkage="ward`
* The best (lowest) *Davies-Bouldin* score is obtained for `affinity="l1` and `linkage="average`
* The best (closer to 1) *Silhoette* score is obtained for `affinity="manhattan` and `linkage="average`. But the before-best score is obtained for the same parameter values of `affinity="l1` and `linkage="average` than for the *Davies-Bouldin* score

An interesting result of the *AgglomerativeClustering* algorithm parameter search, is that when not specifying the number of clusters as a parameter, for all *affinity* and *linkage* values the algorithm computes 2 clusters (below).

In [21]:
hierarchical_results_df[["affinity", "linkage", "n_clusters"]]

affinity   linkage n_clusters
0   euclidean    single          2
1   euclidean   average          2
2   euclidean  complete          2
3   euclidean      ward          2
4          l1    single          2
5          l1   average          2
6          l1  complete          2
7          l2    single          2
8          l2   average          2
9          l2  complete          2
10  manhattan    single          2
11  manhattan   average          2
12  manhattan  complete          2
13     cosine    single          2
14     cosine   average          2
15     cosine  complete          2

For each of the set of parameters, we can compare the resulting clustering by simply taking the most frequent cluster assigned to each Township-Ranges. We can then see some interesting results:
* If we try to optimize for the *Calinski-Harabasz* score (see map in 3rd row, 1st column), we get very similar results as the *K-Means* algorithm, with Township-Ranges in cluster 0 (in blue) located in the South-East mainly aligned along the road 99, between the towns between Madera and Bakersfield.
* Most results fail like *DBSCAN* to compute a meaningful clustering, resulting in 1 big cluster containing almost all Township-Ranges.
* There is one very different clustering result for `affinity=cosine` and `linkage=complete` which is worth investigating.

In [14]:
view_trs_side_by_side(
    get_most_frequent_cluster_for_all_parameters(X_hierarchical, hierarchical_results_df, ["affinity", "linkage"], township_range.sjv_township_range_df, True),
    feature="parameters", value="cluster", title="Comparing the Hierarcical clustering results for each set of paramters", color_scheme="sjv")

alt.ConcatChart(...)